In [1]:
import pandas as pd
import scipy.stats as stats

from sklearn import metrics, model_selection
from catboost import CatBoostClassifier

In [2]:
df_train = pd.read_csv('../../Feature_Encoding/data/train_loo_encoding.csv')
df_test = pd.read_csv('../../Feature_Encoding/data/test_loo_encoding.csv')
train = pd.read_csv('../../Feature_Engineering/data/other-cleaned_train.csv')

In [3]:
def cross_val(model, x_train, y_train):
    score_cross_val = model_selection.cross_val_score(model, x_train, y_train, cv=5)
    print(score_cross_val.mean())

In [4]:
#Realiza busqueda completa combinando los parametros
def catboost(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb = {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.05, 0.1], 'l2_leaf_reg': [0, 1, 5]}    
    catb_gs = model_selection.GridSearchCV(catb_classifier, params_catb, cv=5)
    catb_gs.fit(x_train, y_train)
    catb_best = catb_gs.best_estimator_
    print(catb_gs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [5]:
#Realiza busqueda random dentro de los parametros validos
def catboost2(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb_2={
        'n_estimators':stats.randint(10,500),'learning_rate':stats.uniform(0.01,0.3),
        'subsample':stats.uniform(0.3,0.7),'l2_leaf_reg':[1,5,10],
        'max_depth':[3,10,6],'colsample_bylevel':stats.uniform(0.,0.6)
    }
    
    catb_rs = model_selection.RandomizedSearchCV(CatBoostClassifier(),
                          param_distributions=params_catb_2,
                          cv=2,
                          scoring='neg_log_loss',
                          verbose=1,
                          n_iter=200)
    
    catb_rs.fit(x_train, y_train)
    catb_best = catb_rs.best_estimator_
    print(catb_rs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [6]:
def test_model(model, x_test, y_test):
    predictions = model.predict_proba(x_test)[:,1]
    logloss = metrics.log_loss(y_test, predictions)
    accuracy = metrics.accuracy_score(y_test, predictions.round())
    print("Accuracy: %.2f%%, Logloss: %.2f" % (accuracy*100.0, logloss))

In [7]:
y = train.Target
x_train, x_validation, y_train, y_validation = model_selection.train_test_split(df_train, y, test_size=0.3, stratify=y)

In [8]:
catboost_2 = catboost2(x_train, y_train, x_validation, y_validation)
test_model(catboost_2, x_validation, y_validation)
cross_val(catboost_2, x_train, y_train)

Fitting 2 folds for each of 200 candidates, totalling 400 fits
0:	learn: 0.5064891	total: 80.6ms	remaining: 9.83s
1:	learn: 0.4135941	total: 108ms	remaining: 6.5s
2:	learn: 0.3534365	total: 131ms	remaining: 5.23s
3:	learn: 0.3124528	total: 154ms	remaining: 4.57s
4:	learn: 0.2803360	total: 172ms	remaining: 4.07s
5:	learn: 0.2634528	total: 193ms	remaining: 3.77s
6:	learn: 0.2471243	total: 219ms	remaining: 3.62s
7:	learn: 0.2353792	total: 238ms	remaining: 3.42s
8:	learn: 0.2282829	total: 259ms	remaining: 3.28s
9:	learn: 0.2189358	total: 280ms	remaining: 3.16s
10:	learn: 0.2089919	total: 300ms	remaining: 3.06s
11:	learn: 0.2020075	total: 318ms	remaining: 2.94s
12:	learn: 0.1976738	total: 339ms	remaining: 2.86s
13:	learn: 0.1919886	total: 358ms	remaining: 2.79s
14:	learn: 0.1877220	total: 380ms	remaining: 2.73s
15:	learn: 0.1829161	total: 402ms	remaining: 2.69s
16:	learn: 0.1777308	total: 425ms	remaining: 2.65s
17:	learn: 0.1677975	total: 446ms	remaining: 2.6s
18:	learn: 0.1626455	total: 46

44:	learn: 0.0886511	total: 863ms	remaining: 1.5s
45:	learn: 0.0878209	total: 883ms	remaining: 1.48s
46:	learn: 0.0863587	total: 904ms	remaining: 1.46s
47:	learn: 0.0838571	total: 919ms	remaining: 1.44s
48:	learn: 0.0826759	total: 935ms	remaining: 1.41s
49:	learn: 0.0819700	total: 949ms	remaining: 1.39s
50:	learn: 0.0794086	total: 965ms	remaining: 1.36s
51:	learn: 0.0770262	total: 982ms	remaining: 1.34s
52:	learn: 0.0758630	total: 998ms	remaining: 1.32s
53:	learn: 0.0747163	total: 1.01s	remaining: 1.3s
54:	learn: 0.0741791	total: 1.03s	remaining: 1.27s
55:	learn: 0.0730637	total: 1.05s	remaining: 1.25s
56:	learn: 0.0712717	total: 1.07s	remaining: 1.24s
57:	learn: 0.0687769	total: 1.08s	remaining: 1.22s
58:	learn: 0.0678506	total: 1.1s	remaining: 1.2s
59:	learn: 0.0663202	total: 1.12s	remaining: 1.18s
60:	learn: 0.0652133	total: 1.14s	remaining: 1.16s
61:	learn: 0.0633356	total: 1.16s	remaining: 1.14s
62:	learn: 0.0621619	total: 1.17s	remaining: 1.12s
63:	learn: 0.0615591	total: 1.19s	r

99:	learn: 0.2629462	total: 200ms	remaining: 292ms
100:	learn: 0.2622151	total: 203ms	remaining: 291ms
101:	learn: 0.2616681	total: 206ms	remaining: 291ms
102:	learn: 0.2611624	total: 209ms	remaining: 290ms
103:	learn: 0.2602746	total: 212ms	remaining: 289ms
104:	learn: 0.2598281	total: 214ms	remaining: 287ms
105:	learn: 0.2594428	total: 218ms	remaining: 288ms
106:	learn: 0.2590169	total: 221ms	remaining: 287ms
107:	learn: 0.2587127	total: 223ms	remaining: 285ms
108:	learn: 0.2584024	total: 225ms	remaining: 283ms
109:	learn: 0.2577631	total: 227ms	remaining: 281ms
110:	learn: 0.2572162	total: 229ms	remaining: 279ms
111:	learn: 0.2564939	total: 231ms	remaining: 277ms
112:	learn: 0.2560216	total: 234ms	remaining: 275ms
113:	learn: 0.2555407	total: 236ms	remaining: 273ms
114:	learn: 0.2551840	total: 238ms	remaining: 271ms
115:	learn: 0.2550126	total: 240ms	remaining: 270ms
116:	learn: 0.2546736	total: 243ms	remaining: 268ms
117:	learn: 0.2538154	total: 245ms	remaining: 266ms
118:	learn: 0

27:	learn: 0.3388007	total: 55.3ms	remaining: 431ms
28:	learn: 0.3367753	total: 59ms	remaining: 442ms
29:	learn: 0.3342701	total: 66.1ms	remaining: 476ms
30:	learn: 0.3319422	total: 70ms	remaining: 486ms
31:	learn: 0.3297411	total: 73.1ms	remaining: 489ms
32:	learn: 0.3286875	total: 76.2ms	remaining: 492ms
33:	learn: 0.3273270	total: 78.9ms	remaining: 492ms
34:	learn: 0.3246490	total: 80.8ms	remaining: 487ms
35:	learn: 0.3224003	total: 82.5ms	remaining: 481ms
36:	learn: 0.3214534	total: 84.7ms	remaining: 478ms
37:	learn: 0.3198560	total: 86.5ms	remaining: 473ms
38:	learn: 0.3177443	total: 88.3ms	remaining: 469ms
39:	learn: 0.3159548	total: 90ms	remaining: 464ms
40:	learn: 0.3147368	total: 91.8ms	remaining: 459ms
41:	learn: 0.3131857	total: 93.6ms	remaining: 455ms
42:	learn: 0.3118468	total: 95.6ms	remaining: 451ms
43:	learn: 0.3101473	total: 97.4ms	remaining: 447ms
44:	learn: 0.3088851	total: 99.2ms	remaining: 443ms
45:	learn: 0.3079652	total: 101ms	remaining: 440ms
46:	learn: 0.307032

200:	learn: 0.2383937	total: 453ms	remaining: 101ms
201:	learn: 0.2380316	total: 456ms	remaining: 99.2ms
202:	learn: 0.2377326	total: 458ms	remaining: 97ms
203:	learn: 0.2373028	total: 460ms	remaining: 94.7ms
204:	learn: 0.2367889	total: 462ms	remaining: 92.4ms
205:	learn: 0.2365967	total: 464ms	remaining: 90.2ms
206:	learn: 0.2362429	total: 466ms	remaining: 87.8ms
207:	learn: 0.2357977	total: 468ms	remaining: 85.5ms
208:	learn: 0.2355614	total: 471ms	remaining: 83.3ms
209:	learn: 0.2353004	total: 473ms	remaining: 81.1ms
210:	learn: 0.2349062	total: 475ms	remaining: 78.8ms
211:	learn: 0.2345874	total: 477ms	remaining: 76.5ms
212:	learn: 0.2344247	total: 479ms	remaining: 74.2ms
213:	learn: 0.2341311	total: 481ms	remaining: 71.9ms
214:	learn: 0.2337694	total: 483ms	remaining: 69.6ms
215:	learn: 0.2335367	total: 485ms	remaining: 67.3ms
216:	learn: 0.2334980	total: 487ms	remaining: 65.1ms
217:	learn: 0.2333615	total: 489ms	remaining: 62.9ms
218:	learn: 0.2331082	total: 491ms	remaining: 60.

...

196:	learn: 0.1092877	total: 8.96s	remaining: 12.8s
197:	learn: 0.1089776	total: 9.03s	remaining: 12.8s
198:	learn: 0.1086294	total: 9.06s	remaining: 12.8s
199:	learn: 0.1083705	total: 9.11s	remaining: 12.7s
200:	learn: 0.1081540	total: 9.16s	remaining: 12.7s
201:	learn: 0.1080017	total: 9.22s	remaining: 12.7s
202:	learn: 0.1075529	total: 9.28s	remaining: 12.6s
203:	learn: 0.1073184	total: 9.39s	remaining: 12.7s
204:	learn: 0.1065244	total: 9.43s	remaining: 12.6s
205:	learn: 0.1059456	total: 9.47s	remaining: 12.5s
206:	learn: 0.1057742	total: 9.59s	remaining: 12.6s
207:	learn: 0.1053948	total: 9.64s	remaining: 12.6s
208:	learn: 0.1052020	total: 9.73s	remaining: 12.6s
209:	learn: 0.1048908	total: 9.79s	remaining: 12.5s
210:	learn: 0.1045425	total: 9.84s	remaining: 12.5s
211:	learn: 0.1040779	total: 9.94s	remaining: 12.5s
212:	learn: 0.1038042	total: 9.97s	remaining: 12.4s
213:	learn: 0.1032631	total: 10s	remaining: 12.4s
214:	learn: 0.1030277	total: 10.1s	remaining: 12.4s
215:	learn: 0.

355:	learn: 0.0652512	total: 17.8s	remaining: 6.16s
356:	learn: 0.0648543	total: 17.9s	remaining: 6.13s
357:	learn: 0.0646294	total: 18s	remaining: 6.09s
358:	learn: 0.0644071	total: 18.1s	remaining: 6.04s
359:	learn: 0.0642215	total: 18.1s	remaining: 5.99s
360:	learn: 0.0640551	total: 18.2s	remaining: 5.93s
361:	learn: 0.0638871	total: 18.2s	remaining: 5.88s
362:	learn: 0.0638027	total: 18.2s	remaining: 5.83s
363:	learn: 0.0635223	total: 18.3s	remaining: 5.79s
364:	learn: 0.0632551	total: 18.4s	remaining: 5.74s
365:	learn: 0.0631740	total: 18.5s	remaining: 5.7s
366:	learn: 0.0629154	total: 18.5s	remaining: 5.64s
367:	learn: 0.0628233	total: 18.5s	remaining: 5.59s
368:	learn: 0.0626124	total: 18.6s	remaining: 5.55s
369:	learn: 0.0624664	total: 18.6s	remaining: 5.49s
370:	learn: 0.0623271	total: 18.7s	remaining: 5.44s
371:	learn: 0.0620427	total: 18.7s	remaining: 5.39s
372:	learn: 0.0617733	total: 18.8s	remaining: 5.33s
373:	learn: 0.0617198	total: 18.9s	remaining: 5.3s
374:	learn: 0.06

39:	learn: 0.2309262	total: 1.69s	remaining: 18.5s
40:	learn: 0.2296260	total: 1.72s	remaining: 18.4s
41:	learn: 0.2267529	total: 1.77s	remaining: 18.4s
42:	learn: 0.2254414	total: 1.81s	remaining: 18.4s
43:	learn: 0.2230949	total: 1.86s	remaining: 18.4s
44:	learn: 0.2218042	total: 1.88s	remaining: 18.2s
45:	learn: 0.2204861	total: 1.96s	remaining: 18.4s
46:	learn: 0.2194684	total: 2.02s	remaining: 18.6s
47:	learn: 0.2175916	total: 2.06s	remaining: 18.5s
48:	learn: 0.2158956	total: 2.11s	remaining: 18.5s
49:	learn: 0.2143736	total: 2.15s	remaining: 18.4s
50:	learn: 0.2130345	total: 2.18s	remaining: 18.3s
51:	learn: 0.2120936	total: 2.22s	remaining: 18.2s
52:	learn: 0.2117257	total: 2.22s	remaining: 17.9s
53:	learn: 0.2105068	total: 2.25s	remaining: 17.7s
54:	learn: 0.2091964	total: 2.27s	remaining: 17.5s
55:	learn: 0.2078629	total: 2.3s	remaining: 17.4s
56:	learn: 0.2068078	total: 2.36s	remaining: 17.5s
57:	learn: 0.2059062	total: 2.39s	remaining: 17.3s
58:	learn: 0.2050964	total: 2.42

199:	learn: 0.1078142	total: 10.1s	remaining: 14s
200:	learn: 0.1074129	total: 10.1s	remaining: 14s
201:	learn: 0.1069832	total: 10.2s	remaining: 13.9s
202:	learn: 0.1060721	total: 10.3s	remaining: 14s
203:	learn: 0.1056672	total: 10.3s	remaining: 13.9s
204:	learn: 0.1049380	total: 10.4s	remaining: 13.9s
205:	learn: 0.1047742	total: 10.4s	remaining: 13.8s
206:	learn: 0.1040200	total: 10.5s	remaining: 13.7s
207:	learn: 0.1035280	total: 10.5s	remaining: 13.7s
208:	learn: 0.1031348	total: 10.5s	remaining: 13.6s
209:	learn: 0.1026746	total: 10.6s	remaining: 13.5s
210:	learn: 0.1022759	total: 10.6s	remaining: 13.5s
211:	learn: 0.1018550	total: 10.7s	remaining: 13.4s
212:	learn: 0.1015534	total: 10.7s	remaining: 13.4s
213:	learn: 0.1012987	total: 10.8s	remaining: 13.3s
214:	learn: 0.1010119	total: 10.8s	remaining: 13.3s
215:	learn: 0.1004294	total: 10.9s	remaining: 13.3s
216:	learn: 0.0996244	total: 11s	remaining: 13.3s
217:	learn: 0.0993985	total: 11s	remaining: 13.2s
218:	learn: 0.0989161	

360:	learn: 0.0626430	total: 18.4s	remaining: 6.03s
361:	learn: 0.0625585	total: 18.6s	remaining: 6s
362:	learn: 0.0623530	total: 18.6s	remaining: 5.94s
363:	learn: 0.0622341	total: 18.6s	remaining: 5.88s
364:	learn: 0.0620243	total: 18.7s	remaining: 5.83s
365:	learn: 0.0617317	total: 18.7s	remaining: 5.78s
366:	learn: 0.0616342	total: 18.8s	remaining: 5.74s
367:	learn: 0.0614655	total: 18.8s	remaining: 5.68s
368:	learn: 0.0613539	total: 18.9s	remaining: 5.63s
369:	learn: 0.0610293	total: 18.9s	remaining: 5.57s
370:	learn: 0.0607944	total: 19s	remaining: 5.52s
371:	learn: 0.0605754	total: 19s	remaining: 5.46s
372:	learn: 0.0603441	total: 19s	remaining: 5.41s
373:	learn: 0.0603061	total: 19.1s	remaining: 5.35s
374:	learn: 0.0600183	total: 19.1s	remaining: 5.29s
375:	learn: 0.0599599	total: 19.1s	remaining: 5.24s
376:	learn: 0.0598116	total: 19.2s	remaining: 5.18s
377:	learn: 0.0595981	total: 19.2s	remaining: 5.13s
378:	learn: 0.0592637	total: 19.2s	remaining: 5.07s
379:	learn: 0.0591915

In [9]:
y_pred = catboost_2.predict_proba(df_test)[:,1]
submission_catboost = pd.DataFrame(data={'Opportunity_ID':df_test['Opportunity_ID'], 'Target': y_pred})
submission_catboost = submission_catboost.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_catboost.to_csv('../submits/loo_catboost.csv', index=False)